<a href="https://colab.research.google.com/github/Lxyyxxx/Colab/blob/main/ActorCritic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install loguru

In [2]:
import tensorflow as tf
import numpy as np
import gym
import random
from loguru import logger
from typing import Any, Tuple, List

In [3]:
class ActorModel(tf.keras.Model):
    def __init__(self, action_n: int) -> None:
        super().__init__()
        self.nn = [
            tf.keras.layers.Dense(16, activation='relu'),
            tf.keras.layers.Dense(action_n, activation='softmax'),
        ]

    def call(self, state: Any) -> Any:
        p = state
        for layer in self.nn:
            p = layer(p)
        return p

In [4]:
class CriticModel(tf.keras.Model):
    def __init__(self, action_n: int) -> None:
        super().__init__()
        self.nn = [
            tf.keras.layers.Dense(16, activation='relu'),
            tf.keras.layers.Dense(action_n),
        ]

    def call(self, state: Any) -> Any:
        q = state
        for layer in self.nn:
            q = layer(q)
        return q

image.png

In [5]:
class ActorCriticAgent():
    def __init__(
        self,
        action_n: int,
        alpha_q: float = 0.001,
        alpha_p: float = 0.001, 
        gamma: float = 0.99,
    ) -> None:
        self.action_n = action_n
        self.alpha_q = alpha_q
        self.alpha_p = alpha_p
        self.gamma = gamma
        self.actor_model = ActorModel(action_n)
        self.critic_model = CriticModel(action_n)
    
    def predict(self, state: Any) -> int:
        state = tf.expand_dims(tf.convert_to_tensor(state), 0)
        action = tf.argmax(self.actor_model(state), axis=1).numpy()[0]
        return action

    def learn(self, state: Any, action: int, reward: float, state_: Any, action_: int, done: bool, I: float) -> None:
        state = tf.expand_dims(tf.convert_to_tensor(state), 0)
        state_ = tf.expand_dims(tf.convert_to_tensor(state_), 0)
        # TD error
        q = tf.reduce_sum(tf.multiply(self.critic_model(state), tf.one_hot(action, self.action_n)), axis=1).numpy()
        if done:
            td_error = reward - q
        else:
            q_ = tf.reduce_sum(tf.multiply(self.critic_model(state_), tf.one_hot(action_, self.action_n)), axis=1).numpy()
            td_error = reward + self.gamma * q_ - q
        # critic
        with tf.GradientTape() as tape:
            q_loss = tf.reduce_sum(tf.multiply(self.critic_model(state), tf.one_hot(action, self.action_n)), axis=1)
        q_grads = tape.gradient(q_loss, self.critic_model.trainable_weights)
        for v, g in zip(self.critic_model.trainable_weights, q_grads):
            v.assign_add(self.alpha_q * td_error * g)
        # actor
        with tf.GradientTape() as tape:
            p = self.actor_model(state)
            p_loss = tf.math.log(p)
        p_grads = tape.gradient(p_loss, self.actor_model.trainable_weights)
        for v, g in zip(self.actor_model.trainable_weights, p_grads):
            v.assign_add(self.alpha_p * I * td_error * g)

    def save_model(self) -> None:
        self.actor_model.save('actor')
        self.critic_model.save('critic')

    def load_model(self) -> None:
        self.actor_model = tf.keras.models.load_model('actor')
        self.critic_model = tf.keras.models.load_model('critic')

In [6]:
def run_episode(env: gym.Wrapper, agent: ActorCriticAgent, training: bool, batch_size: int = 32, render: bool = False) -> float:
    state = env.reset()
    done = False
    score = 0
    I = 1
    while not done:
        if render:
            env.render()
        action = agent.predict(state)
        state_, reward, done, info = env.step(action)
        score += reward
        if training:
            action_ = agent.predict(state_)
            agent.learn(state, action, reward, state_, action_, done, I)
        I *= agent.gamma
        state = state_
    return score

In [7]:
def train(env: gym.Wrapper, agent: ActorCriticAgent) -> None:
    score_result = []
    max_score = 0
    for episode in range(1000):
        score = run_episode(env, agent, training=True)
        score_result.append(score)
        if score > max_score:
            max_score = score
            logger.info('Episode {}: Best score {}'.format(episode, score))
        if score == max_score:
            agent.save_model()
        if episode % 50 == 0:
            logger.info('Episode {}: score {}'.format(episode, score))

    plt.title('Train Score Curve')
    plt.xlabel('Episode')
    plt.ylabel('Score')
    plt.plot(score_result, label='$Score$')
    plt.legend()
    plt.show()

def play(env: gym.Wrapper, agent: ActorCriticAgent) -> None:
    score_result = []
    agent.load_model()
    for episode in range(5):
        score = run_episode(env, agent, training=False, render=False)
        score_result.append(score)
        logger.info('Round {}: score: {}'.format(episode, score))
    
    plt.title('Play Score Curve')
    plt.xlabel('Round')
    plt.ylabel('Score')
    plt.plot(score_result, label='$Score$')
    plt.legend()
    plt.show()

In [8]:
if __name__ == '__main__':
    import matplotlib.pyplot as plt

    env = gym.make('CartPole-v0')
    agent = ActorCriticAgent(env.action_space.n)
    # train
    train(env, agent)
    # play
    play(env, agent)

2021-10-03 08:31:40.319 | INFO     | __main__:train:9 - Episode 0: Best score 108.0


INFO:tensorflow:Assets written to: actor/assets
INFO:tensorflow:Assets written to: critic/assets


2021-10-03 08:31:41.264 | INFO     | __main__:train:13 - Episode 0: score 108.0
2021-10-03 08:31:43.140 | INFO     | __main__:train:9 - Episode 1: Best score 200.0


INFO:tensorflow:Assets written to: actor/assets
INFO:tensorflow:Assets written to: critic/assets
INFO:tensorflow:Assets written to: actor/assets
INFO:tensorflow:Assets written to: critic/assets
INFO:tensorflow:Assets written to: actor/assets
INFO:tensorflow:Assets written to: critic/assets
INFO:tensorflow:Assets written to: actor/assets
INFO:tensorflow:Assets written to: critic/assets


2021-10-03 08:32:11.954 | INFO     | __main__:train:13 - Episode 50: score 22.0


INFO:tensorflow:Assets written to: actor/assets
INFO:tensorflow:Assets written to: critic/assets
INFO:tensorflow:Assets written to: actor/assets
INFO:tensorflow:Assets written to: critic/assets


2021-10-03 08:32:35.236 | INFO     | __main__:train:13 - Episode 100: score 24.0
2021-10-03 08:32:52.536 | INFO     | __main__:train:13 - Episode 150: score 29.0
2021-10-03 08:33:08.359 | INFO     | __main__:train:13 - Episode 200: score 48.0
2021-10-03 08:33:22.998 | INFO     | __main__:train:13 - Episode 250: score 26.0
2021-10-03 08:33:32.578 | INFO     | __main__:train:13 - Episode 300: score 16.0
2021-10-03 08:33:42.099 | INFO     | __main__:train:13 - Episode 350: score 23.0
2021-10-03 08:33:51.562 | INFO     | __main__:train:13 - Episode 400: score 23.0
2021-10-03 08:34:00.719 | INFO     | __main__:train:13 - Episode 450: score 16.0
2021-10-03 08:34:09.599 | INFO     | __main__:train:13 - Episode 500: score 17.0
2021-10-03 08:34:17.087 | INFO     | __main__:train:13 - Episode 550: score 16.0
2021-10-03 08:34:23.739 | INFO     | __main__:train:13 - Episode 600: score 12.0
2021-10-03 08:34:29.375 | INFO     | __main__:train:13 - Episode 650: score 12.0
2021-10-03 08:34:34.367 | IN

2021-10-03 08:35:03.136 | INFO     | __main__:play:28 - Round 0: score: 23.0
2021-10-03 08:35:03.165 | INFO     | __main__:play:28 - Round 1: score: 29.0
2021-10-03 08:35:03.194 | INFO     | __main__:play:28 - Round 2: score: 28.0
2021-10-03 08:35:03.222 | INFO     | __main__:play:28 - Round 3: score: 22.0
2021-10-03 08:35:03.260 | INFO     | __main__:play:28 - Round 4: score: 34.0


梯度爆炸
image.png